In [1]:
# !cp -rf /content/drive/MyDrive/ML\ Projects/Gemini-Pro/docs /content/

In [1]:
# !pip install langchain
# !pip install pypdf
# !pip install langchain_google_genai
# !pip install google-generativeai
# !pip install chromadb
# !pip install gradio
# !pip install faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 KB 604.5 kB/s eta 0:00:00a 0:00:01
  Using cached tenacity-8.2.3-py3-none-any.whl (24 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 1.7 MB/s eta 0:00:0000:0100:01
  Using cached requests-2.31.0-py3-none-any.whl (62 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 2.0 MB/s eta 0:00:0000:0100:01
  Using cached langchain_core-0.1.10-py3-none-any.whl (216 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 1.1 MB/s eta 0:00:00eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 KB 594.8 kB/s eta 0:00:00 0:00:01
  Using cached PyYAML-6.0.1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (705 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 524.5 kB/s eta 0:00:0000:0100:04
  Using cached async_timeout-4.0.3-py3-none-any.whl (5.7 kB)
  Using cached pydantic-2.5.3-py3-none-any.whl (381 kB)
  Using cached jsonpatch-1.33-py2.py3-none-any.whl (12 kB)
  Using cached aio

In [3]:
import os
from langchain.document_loaders import (
    PyPDFLoader,
    TextLoader,
    Docx2txtLoader
)

from langchain.text_splitter import CharacterTextSplitter
# from PyPDF2 import PdfReader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_google_genai import GoogleGenerativeAIEmbeddings
import google.generativeai as genai
from langchain.vectorstores import FAISS
from langchain_google_genai import ChatGoogleGenerativeAI
from langchain.chains.question_answering import load_qa_chain
from langchain.prompts import PromptTemplate
from langchain.memory import ConversationBufferMemory
from dotenv import load_dotenv
load_dotenv()

True

In [6]:
def extract_text(docs):
    documents = []
    files = os.listdir(docs)
    
    if len(files) == 0:
        return "Directory is empty"

    base_dir = docs.split("/")
    base_dir = "/".join(base_dir)

    for file in files:
        if file.endswith(".pdf"):
            pdf_path=os.path.join(base_dir, file)
            loader=PyPDFLoader(pdf_path)
            documents.extend(loader.load())
        elif file.endswith('.docx') or file.endswith('.doc'):
            doc_path=os.path.join(base_dir, file)
            loader=Docx2txtLoader(doc_path)
            documents.extend(loader.load())
        elif file.endswith('.txt'):
            text_path=os.path.join(base_dir, file)
            loader=TextLoader(text_path)
            documents.extend(loader.load())
    return documents

In [7]:
doc_dir = "../docs"

In [8]:
documents = extract_text(doc_dir)

['profile.txt', 'llm-research.pdf']
../docs


In [9]:
def get_text_chunks(text):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=10000, chunk_overlap=1000)
    chunks = text_splitter.split_documents(text)
    return chunks

def save_in_faiss(text_chunks, save=False):
    embeddings = GoogleGenerativeAIEmbeddings(model = "models/embedding-001")
    vector_store = FAISS.from_documents(text_chunks, embedding=embeddings)
    if not save:
        vector_store.save_local("faiss_index")
    return vector_store

In [10]:
def process_files(docs):
    documents = extract_text(docs)
    text_chunks = get_text_chunks(documents)
    vector_store = save_in_faiss(text_chunks)
    return vector_store

In [17]:
llm = model = ChatGoogleGenerativeAI(model="gemini-pro",temperature=0.7)

template = """You are a chatbot having a conversation with a human.

Given the following extracted parts of a long document and a question, create a final answer.

{context}

{chat_history}
Human: {human_input}
Chatbot:"""

prompt = PromptTemplate(
    input_variables=["chat_history", "human_input", "context"], template=template
)
memory = ConversationBufferMemory(memory_key="chat_history", input_key="human_input")
chain = load_qa_chain(
    llm=llm, chain_type="stuff", memory=memory, prompt=prompt
)

In [ ]:
def build_qa_chain(llm=llm, prompt=prompt, memory=memory):
    chain = load_qa_chain(
    llm=llm, chain_type="stuff", memory=memory, prompt=prompt
)
    return chain

def build_agent(query, db):
    query = "is vasim plumber"
    docs = db.similarity_search(query)
    response = chain({"input_documents": docs, "human_input": query}, return_only_outputs=True)
    return response['output_text']

In [12]:
db = process_files(doc_dir)

['profile.txt', 'llm-research.pdf']
../docs


In [16]:
query = "is vasim plumber"
docs = db.similarity_search(query)
chain({"input_documents": docs, "human_input": query}, return_only_outputs=True)

{'output_text': 'I do not have any information about Vasim being a plumber.'}

In [18]:
def answer_query(message, history):
    docs = db.similarity_search(message)
    response = chain({"input_documents": docs, "human_input": message}, return_only_outputs=True)
    return response['output_text']

In [34]:
# Gradio App
import gradio as gr

title = ""
description = f"Chat with any docs"

# def answer_query(message, history):
#     docs = db.similarity_search(message)
#     message = agent(
#         {"input_documents":docs, "question": message}
#         ,return_only_outputs=True)
#     return message['output_text']


chatbot = gr.Chatbot(label="ExploreText")

with gr.Blocks(
    title="ExploreText",
    ) as textbot:

    gr.Markdown("# <center> Welcome to ExploreDoc Web App</center>")
    
    with gr.Accordion("Upload a file here", open=False):
        file_output = gr.File(scale=1)
        upload_button = gr.UploadButton("Click to Upload a File", file_types=["txt","doc","pdf"])
        upload_button.upload(process_files, upload_button, file_output)
        # gr.Info("Click on Chat with PDF tab")

    # with gr.Row("Chat with Text"):
    gr.ChatInterface(fn=answer_query, chatbot=chatbot, submit_btn="Ask", undo_btn=None, retry_btn=None, clear_btn=None)
    print("Chat interface is cool.")
    gr.Markdown("<center>  Developed by <a href='https://92-vasim.github.io' target='_blank'>Mohammed Vasim<a/> | AI Engineer & Computer Vision Engineer @ ZestIoT.  </center>")
        

if __name__ == "__main__":
    textbot.queue().launch()



Chat interface is cool.
Running on local URL:  http://127.0.0.1:7875

To create a public link, set `share=True` in `launch()`.
